In [4]:
using Revise
using Astroshaper

In [5]:
using Plots
using DataFrames

In [6]:
using BenchmarkTools
using StaticArrays
using StructArrays
using LinearAlgebra
using Parameters

In [22]:
shapedir = "/Users/masanorikanamaru/Documents/shape/ryugu"

shapename = "ryugu_v252_f500.obj"
# shapename = "ryugu_v752_f1500.obj"
# shapename = "ryugu_test.obj"

# shapename = "SHAPE_SPC_49k_v20190802.obj"
# shapename = "SHAPE_SPC_200k_v20190802.obj"
# shapename = "SHAPE_SPC_800k_v20190802.obj"
# shapename = "SHAPE_SPC_3M_v20190802.obj"

# shapename = "SHAPE_SFM_49k_v20180804.obj"
# shapename = "SHAPE_SPC_49k_v20200323.obj"
# shapename = "SHAPE_SPC_3M_v20200323.obj"

shapepath = joinpath(shapedir, shapename)
@show shapepath;

shapepath = "/Users/masanorikanamaru/Documents/shape/ryugu/ryugu_v252_f500.obj"


In [23]:
@time shape = setShapeModel(shapepath; scale=1000, find_visible_faces=true, save_shape=true)

# shape = setShapeModel(splitext(shapepath)[1] * ".jld2")

  0.014506 seconds (56.88 k allocations: 3.914 MiB)


Shape model


-----------
Nodes            : 252
Faces            : 500
Surface area     : 2.674022248237023e6
Volume           : 3.7596997192847484e8
Center-of-Figure : [0.3711582968055714, 0.1430131803740257, 0.02972401268611604]
Inertia tensor   : 
    | Ixx Ixy Ixz |   [0.0, 0.0, 0.0]
    | Iyx Iyy Iyz | = [0.0, 0.0, 0.0]
    | Izx Izy Izz |   [0.0, 0.0, 0.0]


In [24]:
params_orbit = Dict()

params_orbit[:a] = 1.18956373  # semi-mojor axis [AU]
params_orbit[:e] = 0.19027921  # eccentricity
params_orbit[:I] = 5.8840222   # inclination [deg]
params_orbit[:Ω] = 251.589203  # longitude of the ascending node [deg]
params_orbit[:ω] = 211.435963  # argument of periapsis [deg]
params_orbit[:Φ] = 21.9353799  # mean anomaly [deg]

params_orbit[:μ] = GM☉ + 30.0

orbit = OrbitalElements(params_orbit)

Orbital elements
----------------


Semi-mojor axis        : a  = 1.18956373 [AU]
Eccentricity           : e  = 0.19027921 [-]
Lon. of ascending node : Ω  = 251.589203 [deg]
Argument of periapsis  : ω  = 211.435963 [deg]
Inclination            : I  = 5.8840222 [deg]
Periapsis passage time : tₚ = -2.4948038004043424e6 [sec]
Mean anomaly           : Φ  = 21.9353799 [deg]

Other parameters
----------------
Gravitational parameter : μ = 1.32712440018e20 [m^3/s^2]
Mean motion             : n = 0.7596656791419168 [deg/day]
Orbital period          : T = 473.8926739544681 [day]


In [25]:
params_spin = Dict()
params_spin[:α] = 96.4
params_spin[:δ] = -66.4
params_spin[:T] = 7.63262

spin = setSpinParams(params_spin, orbit)

Spin parameters
---------------


Right ascension (RA) : α = 96.4 [deg]
Declination (Dec)    : δ = -66.4 [deg]
Ecliptic longitude   : λ = 179.33757188938182 [deg]
Ecliptic latitude    : β = -87.44207056697601 [deg]
Obliquity            : ε = 171.65664649001607 [deg]
Spin period          : P = 7.63262 [hours]
Spin rate            : ω = 0.00022866712242903872 [rad/sec]
Vernal equinox lon.  : γ = 154.3323208882217 [deg]
                           (longitude from the periheion direction)


In [26]:
params_thermo = ParamsThermo(
    A_B   = 0.04,
    A_TH  = 0.,
    k     = 0.1,
    ρ     = 1270.,
    Cₚ    = 600.,
    ϵ     = 1.,
    P     = spin.T,
    Δt    = spin.T/72,
    t_bgn = 0.,
    # t_end = spin.T*10,
    t_end = orbit.T,
    Δz    = 0.015,
    z_max = 0.6,
)

Thermophysical parameters


-------------------------
A_B   : 0.04
A_TH  : 0.0
k     : 0.1
ρ     : 1270.0
Cₚ    : 600.0
ϵ     : 1.0
P     : 27477.432
l     : 0.21287051812296282
Γ     : 276.04347483684523
Δt    : 0.01388888888888889
t_bgn : 0.0
t_end : 1490.1074827395094
Nt    : 107288
Δz    : 0.07046537083794469
z_max : 2.8186148335177874
Nz    : 41
λ     : 0.22259025955088954


In [27]:
@time τ̄ = run_YORP(shape, orbit, spin, params_thermo)

#   0.197834 seconds (2 allocations: 224 bytes)

# 3-element Vector{Float64}:
#   2.3738673604758747
#  -8.242315949107525
#  -0.7373576061313664

 27.259630 seconds (3.39 M allocations: 196.512 MiB, 0.12% gc time, 2.81% compilation time)


3-element Vector{Float64}:
  2.1021409943529754
 -1.9503714305184237
  0.10649921391003535

In [28]:
C = 4.039541372643629e16
ω̇, ωε̇, ωψ̇ = torque2rate(τ̄, spin, C)  # [deg/day/day]

@show shapename
@show τ̄
@show ω̇, ωε̇, ωψ̇
@show getTimeScale(3.5, 7.63262, ω̇);  # 3.5時間から7.6時間まで減速する時間スケール [Myr]

shapename = "ryugu_v252_f500.obj"
τ̄ = [2.1021409943529754, -1.9503714305184237, 0.10649921391003535]
(ω̇, ωε̇, ωψ̇) = (-2.417573363465429e-6, 8.71343482743634e-6, 2.9006203791289243e-5)
getTimeScale(3.5, 7.63262, ω̇) = 1.5146943442921814


In [29]:
@time Fs = run_Yarkovsky(shape, orbit, spin, params_thermo)

 26.750153 seconds (179.78 k allocations: 17.702 MiB, 0.12% compilation time)


107288-element Vector{Vector{Float64}}:
 [9.920246219963175e-6, 4.4496328351317885e-6, 6.012222964351851e-7]
 [0.02514336141450109, 0.01326815113898024, -0.001815071663836259]
 [0.05105872795845857, 0.025989023641714647, -0.0036973252438783537]
 [0.07874929434195277, 0.03818524847361166, -0.005670679983287378]
 [0.10640491332632096, 0.04878584187773018, -0.007639109581510975]
 [0.13308299095354126, 0.057345973600436195, -0.009569675784070975]
 [0.15820719805370836, 0.06376971664208476, -0.011463791498545896]
 [0.1814717940491656, 0.06797464413172702, -0.013319770105119325]
 ⋮
 [0.7047151720579292, 0.1892429229494164, -0.10054282407351449]
 [0.705329000117082, 0.18730869783683327, -0.09967155138436107]
 [0.7061512892167515, 0.18331873863691572, -0.09859567817579652]
 [0.7064730698770786, 0.1784615028271097, -0.09722925250099049]
 [0.7055954254047088, 0.175050826138852, -0.09305709270305697]
 [0.7032717639166238, 0.1741448127191045, -0.08914039779598515]
 [0.7017673567810998, 0.170871417

In [30]:
sum(Fs)

3-element Vector{Float64}:
 2981.0076307424197
 -249.01689102916134
  315.45746102019905

In [153]:
sum(Fs)

3-element Vector{Float64}:
 2982.3071756486106
 -219.976692638209
  152.3711104465482

In [207]:
Fs  # Orbital plane frame

107288-element Vector{Vector{Float64}}:
 [1.677735064871607e-5, 9.12543760850991e-6, -8.828890575542383e-7]
 [0.025540335144384085, 0.013429405880621317, -0.001692796811481751]
 [0.05178317489032352, 0.026209267089878217, -0.003425283278107239]
 [0.07976463945174009, 0.03847626262624043, -0.005326257312058059]
 [0.10765551354972769, 0.04907820933497722, -0.007176999086802039]
 [0.1345224813790569, 0.05760143985530128, -0.008978460734079232]
 [0.159785772153509, 0.06393467374295483, -0.010706635428011504]
 [0.18310869976622668, 0.06810367448470052, -0.012333874156540182]
 ⋮
 [0.7042544088183204, 0.19083803941021396, -0.10410469688603334]
 [0.7048664378970755, 0.18819846121930195, -0.10303161808549388]
 [0.7060763642253584, 0.18480893912898963, -0.1022844013977783]
 [0.7062531006253394, 0.1803090005462702, -0.10026409805977719]
 [0.705382163221593, 0.17664463322242682, -0.09693117368416927]
 [0.7039911164900992, 0.17416276050940052, -0.09286527948819683]
 [0.7029520425665382, 0.170467050

In [208]:
@unpack P, Δt, t_bgn, t_end = params_thermo
ts = collect( (t_bgn:Δt:t_end)*P )

us = Float64[]  # eccentric anomaly
fs = Float64[]  # true anomaly
for t in ts
    u = Astroshaper.solveKeplerEquation2(orbit, t)
    f = Astroshaper.u2ν(u, orbit.e)
    push!(us, u)
    push!(fs, f)
end

In [210]:
_Fs = Vector{Float64}[]
for (f, F) in zip(fs, Fs)
    _F = rotateZ(SVector{3}(F), f)
    push!(_Fs, _F)
end

In [217]:
_Fs

107288-element Vector{Vector{Float64}}:
 [1.9057575671718825e-5, -1.2497663195539093e-6, -8.828890575542383e-7]
 [0.0287643384331434, -0.0022957561058433076, -0.001692796811481751]
 [0.05777494463991989, -0.0055207476816639435, -0.003425283278107239]
 [0.08798034760496387, -0.010113304497504631, -0.005326257312058059]
 [0.11721836901775297, -0.016069666891424327, -0.007176999086802039]
 [0.14447877556619598, -0.02324020827521498, -0.008978460734079232]
 [0.16921182990778866, -0.031408471923491756, -0.010706635428011504]
 [0.19114655992937973, -0.04037200806945626, -0.012333874156540182]
 ⋮
 [0.69739588695145, -0.21455164061171064, -0.10410469688603334]
 [0.6964863229938048, -0.21716850131083526, -0.10303161808549388]
 [0.6956814432212505, -0.22073854592544914, -0.1022844013977783]
 [0.6934094618238367, -0.22469556309388475, -0.10026409805977719]
 [0.6906973430299818, -0.2273862418194721, -0.09693117368416927]
 [0.6881767103376966, -0.22879898293921053, -0.09286527948819683]
 [0.6853049

In [261]:
@unpack P, Δt, t_bgn, t_end = params_thermo
ts = collect( (t_bgn:Δt:t_end)*P )
M = 30.0 / G

df = DataFrame(t=Float64[], u=Float64[], r=Float64[], f=Float64[], a_R=Float64[], a_T=Float64[], a_N=Float64[])

for (t, F) in zip(ts, Fs)
    u = Astroshaper.solveKeplerEquation2(orbit, t)
    r = norm(Astroshaper.get_r(orbit, u))
    f = Astroshaper.u2ν(u, orbit.e)
    _F = rotateZ(SVector{3}(F), f)
    
    push!(df, (t, u, r, f, _F[1]/M, _F[2]/M, _F[3]/M))
end

In [262]:
df

107288×7 DataFrame
    Row │ t             u         r           f          a_R          a_T           a_N          
        │ Float64       Float64   Float64     Float64    Float64      Float64       Float64      
────────┼────────────────────────────────────────────────────────────────────────────────────────
      1 │    0.0        0.468819  1.47748e11   0.563643  4.23973e-17  -2.78035e-18  -1.96416e-18
      2 │  381.631      0.46889   1.47749e11   0.563727  6.39919e-14  -5.10736e-15  -3.76596e-15
      3 │  763.262      0.46896   1.47751e11   0.56381   1.28532e-13  -1.2282e-14   -7.62021e-15
      4 │ 1144.89       0.469031  1.47752e11   0.563894  1.95729e-13  -2.2499e-14   -1.18493e-14
      5 │ 1526.52       0.469101  1.47753e11   0.563977  2.60775e-13  -3.57501e-14  -1.59666e-14
      6 │ 1908.16       0.469172  1.47754e11   0.56406   3.21421e-13  -5.17024e-14  -1.99743e-14
   ⋮    │      ⋮           ⋮          ⋮           ⋮           ⋮            ⋮             ⋮
 107284 │    4.09425e7  6.75167   1.47743e11  -5.71994   1.54768e-12  -4.91076e-13  -2.27552e-13
 107285 │    4.09429e7  6.75174   1.47744e11  -5.71985   1.54262e-12  -4.99879e-13  -2.23057e-13
 107286 │    4.09433e7  6.75181   1.47745e11  -5.71977   1.53659e-12  -5.05865e-13  -2.15642e-13
 107287 │    4.09437e7  6.75188   1.47747e11  -5.71969   1.53098e-12  -5.09008e-13  -2.06597e-13
 107288 │    4.0944e7   6.75195   1.47748e11  -5.7196    1.52459e-12  -5.14851e-13  -1.9707e-13
                                                                              107277 rows omitted

In [288]:
df.drift_R = @. 2 / orbit.n / √(1 - orbit.e^2) * orbit.e * sin(df.f) * df.a_R
df.drift_T = @. 2 / orbit.n / √(1 - orbit.e^2) * orbit.a * (1 - orbit.e^2) / df.r * df.a_T

df.drift_total = @. df.drift_R + df.drift_T

107288-element Vector{Float64}:
  1.4371675748432316e-11
  7.666452383756174e-9
 -1.5761377227084923e-8
 -8.246102108536812e-8
 -1.9879637038282418e-7
 -3.6267304306880505e-7
 -5.683235712093548e-7
 -8.096240218566256e-7
  ⋮
 -5.264112989445659e-6
 -5.356232981793645e-6
 -5.480718763338009e-6
 -5.622873601842465e-6
 -5.722932747423947e-6
 -5.778604023727529e-6
 -5.876942818637065e-6

In [297]:
plot(framestyle=:box, legend=:bottomleft)
plot!(xlims=(0, orbit.T/3600/24))
# plot!(ylims=(-1.2, 1.2))

# hline([mean(df.drift_total)*3600*24*365], label=false)

plot!(df.t/3600/24, df.drift_R*3600*24*365, label="Radial",)
plot!(df.t/3600/24, df.drift_T*3600*24*365, label="Tranverse")
plot!(df.t/3600/24, df.drift_total*3600*24*365, label="Total")
# plot!([0], [0], marker=(:plus, 5, :black))
# scatter!(xs, ys, marker=(:circle, 0.8, 1, :blue, stroke(0, 0.2, :black, :dot)))

In [296]:
mean(df.drift_total)*3600*24*365

-138.60899939804943